In [1]:

import bokeh.plotting as bpl
import cv2
import glob
import logging
import matplotlib.pyplot as plt
import numpy as np
import os
import tifffile as tif

try:
    cv2.setNumThreads(0)
except():
    pass

try:
    if __IPYTHON__:
        # this is used for debugging purposes only. allows to reload classes
        # when changed
        get_ipython().magic('load_ext autoreload')
        get_ipython().magic('autoreload 2')
except NameError:
    pass

import caiman as cm
from caiman.motion_correction import MotionCorrect
from caiman.source_extraction.cnmf import cnmf as cnmf
from caiman.source_extraction.cnmf import params as params
from caiman.utils.utils import download_demo
from caiman.utils.visualization import plot_contours, nb_view_patches, nb_plot_contour

from caiman.source_extraction import cnmf as cnmf
from scipy.sparse import csc_matrix

import h5py
bpl.output_notebook()

C:\Anaconda3\envs\py36\lib\site-packages\scipy\ndimage\morphology.py:114: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  out[slc] = structure != 0


Loading BokehJS ...

In [15]:
hf = h5py.File('C:/Users/bnste/Documents/scripts/jon_2p_data/analysis.hdf5')
cnm = list(hf.values())
 cnmf.

[<HDF5 dataset "M": shape (), type "<i4">,
 <HDF5 dataset "N": shape (), type "<i4">,
 <HDF5 dataset "cnn_pos": shape (0, 50, 50), type "<f4">,
 <HDF5 dataset "comp_upd": shape (15800,), type "<i4">,
 <HDF5 dataset "dims": shape (2,), type "<i4">,
 <HDF5 group "/estimates" (44 members)>,
 <HDF5 dataset "img_min": shape (), type "<f4">,
 <HDF5 dataset "img_norm": shape (512, 512), type "<f4">,
 <HDF5 dataset "ind_new_all": shape (10, 2, 2), type "<i8">,
 <HDF5 group "/params" (10 members)>,
 <HDF5 dataset "rhos_buf": shape (100, 262144), type "<f4">,
 <HDF5 dataset "t_detect": shape (15800,), type "<f8">,
 <HDF5 dataset "t_motion": shape (15800,), type "<f8">,
 <HDF5 dataset "t_online": shape (15800,), type "<f8">,
 <HDF5 dataset "t_shapes": shape (15800,), type "<f8">,
 <HDF5 dataset "time_neuron_added": shape (30, 2), type "<i4">,
 <HDF5 dataset "time_spend": shape (), type "<f8">,
 <HDF5 dataset "update_counter": shape (30,), type "<f4">]

In [24]:
cnm.estimates.nb_view_components()

In [22]:
cnm = cnmf.online_cnmf.load_OnlineCNMF('C:/Users/bnste/Documents/scripts/jon_2p_data/analysis.hdf5')

C:\Anaconda3\envs\py36\lib\site-packages\scipy\ndimage\morphology.py:114: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  out[slc] = structure != 0


In [26]:
cnmf.params.CNMFParams?

In [29]:

def cellInfoCaimanHdf5(hdf5File):
    """
    Given a CaImAn output .hdf5 file, returns the spatial cell profiles, cell signal traces, and background profiles and traces
    Output:
    (cellProfs, signalTraces, bgProfs, bgTraces)
    cellProfs is a numCells x xDim x yDim array of spatial cell profiles
    signalTraces is a  tBins x numCells array of fluorescence traces from each cell
    bgProfs: nBGComps x xDim x yDim
    bgTraces: tBins x nBGComps
    """
    cellProfs = []
    signalTraces = []

    with h5py.File(hdf5File, mode='r') as cFile:
        est = cFile['estimates']
        Ainfo = est['A']
        signalTraces = np.transpose( np.array(est['C']) )
        Adata = np.array(Ainfo['data'])
        Aindices = np.array(Ainfo['indices'])
        Aindptr = np.array(Ainfo['indptr'])
        Ashape = np.array(Ainfo['shape'])
        A = csc_matrix((Adata,Aindices,Aindptr) , shape=Ashape ).transpose()
        A = np.array(A.todense())
        cellProfs = A.reshape((A.shape[0],np.array(est['dims'])[0] ,-1))
        f = np.array(est['f']).transpose()
        b = np.array(est['b']).transpose()
        b = b.reshape(b.shape[0],cellProfs.shape[1],cellProfs.shape[2])
    return (cellProfs, signalTraces, b, f)

A, C, b, f = cellInfoCaimanHdf5('C:/Users/bnste/Documents/scripts/jon_2p_data/analysis.hdf5')

In [31]:
mov = np.tensordot(C[:300], A, (-1,0) ).transpose((0,2,1))
mov_cm = cm.movie(mov, fr=10)
mov_cm.play(magnification=2, gain=2)

In [2]:
%run process_scanimage_chunks.py

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
Processing movie file C:\Users\bnste\Documents\scripts\jon_2p_data\JG24831_181210_field1_behavior_00001_00001.tif
Processing channel 0
Removed 6 bad frames from file C:\Users\bnste\Documents\scripts\jon_2p_data\JG24831_181210_field1_behavior_00001_00001.tif, channel 0



TypeError: unsupported operand type(s) for +: 'int' and 'str'

In [11]:
tif.imsave('C:\\Users\\bnste\\Documents\\scripts\\jon_2p_data\\test_channel_0.tif', data=ch_mov[:100], imagej=True)

In [7]:
ch_out_file

'C:\\Users\\bnste\\Documents\\scripts\\jon_2p_data\\JG24831_181210_field1_behavior_00001_00001_channel_0.tif'

In [6]:
testmov = cm.movie(ch_mov[:,0,:,:], fr=30)
testmov.play(magnification=2, gain=3)